In [1]:
%load_ext autoreload
%autoreload 2

In [17]:
from functools import partial

from kelly_criterion.benchmarks import run_estimator_benchmark
from kelly_criterion.estimators import make_saa_estimator
from kelly_criterion.kelly import univariate_log_return
from kelly_criterion.kelly import univariate_log_return_to_minimize
from kelly_criterion.plots import plot_benchmark_stats
from kelly_criterion.plots import plot_func
from kelly_criterion.plots import plot_sampled_func
from kelly_criterion.samplers import make_bernoulli_return_sampler

# Solving for the Kelly Strategy

## Objective

The goal of this lab is to explore some ways of solving for the Kelly Strategy. Despite the simple statement of the strategy, it seems to be non-obvious to evaluate even if we assume a given distribution. 

## Background


### Binomial Case

The Kelly Strategy is to maximize the expected log-returns per period, $G(\Lambda) := \mathbb{E}\big[ \log\big( X(\Lambda) \big)\big]$, over all eligible strategies $\Lambda$.

In the binomial case initially presented by Kelly, we get a closed-form solution:

$$
\begin{align}
& G(\Lambda) = G(\lambda) = \mathbb{E}\big[ \log\big( (1-\lambda) +\lambda X \big)\big] = p \log(1+\lambda) + q \log(1-\lambda) \\
& \Rightarrow \lambda^* := \arg\max_\lambda G(\lambda) = p-q
\end{align}
$$

This will be the reference case to compare any solution algorithms.

### General Univariate Case

If we just extend that same univariate case to a general distribution there no longer seems to be a closed-form solution:

$$
G(\Lambda) = G(\lambda) = \mathbb{E}\big[ \log\big( (1-\lambda) +\lambda X \big)\big] = \mathbb{E}\big[ \log\big( 1 + \lambda (X-1) \big)\big] = \mathbb{E}\big[ \log\big( 1 + \lambda R \big)\big]
$$


Note:
- We use $R := X-1$ (the absolute return of the unit risky asset) to simplify some notation. Here we're assuming $R > -1$.
- In a number of references, there's a risk-free rate of growth $r$. As long as $r$ is non-random, it washes out by using $e^{rt}$ as numeraire. So $X$ is really $e^{rt}X$. But this isn't relavant to the exploration here.

We'll restrict attention here just to this univariate case.

### Optimum

If there is suitable integrability, we have

$$
\begin{align}
G(\lambda) &= \mathbb{E}\big[ \log\big( 1 + \lambda R \big)\big] \\
G'(\lambda) &= \frac{d}{d\lambda} \mathbb{E}\big[ \log\big( 1 + \lambda R \big)\big] = \mathbb{E}\big[ \frac{d}{d\lambda} \log\big( 1 + \lambda R \big)\big] = \mathbb{E}\big[ \frac{R}{1+\lambda R} \big] \\
G''(\lambda) &= \mathbb{E}\big[ \frac{-R^2}{(1+\lambda R)^2)} \big] < 0 \\
\end{align}
$$

so expect a unique optimum and a convex function.

We'll call the optimal fraction $\lambda^* := \arg \max_\lambda G(\lambda)$.


## Taylor Approximation

Taking a second-order approximation of the log, we get:

$$
G(\lambda) = \mathbb{E}\big[ \log\big( 1 + \lambda R \big)\big] = \mathbb{E}\big[ \lambda R - \frac{1}{2} \big(\lambda (R\big)^2 \big] = \lambda \mu - \frac{1}{2} \lambda^2 \sigma^2
$$

where
- $\mu := \mathbb{E}[R]$ is the expected return of the variable
- $\sigma^2 := \mathbb{E}[R^2]$ is the second (non-central) moment of the return of the variable

This gives $\lambda^* = \frac{\mu}{\sigma^2}$.

#### In the binomial case

$$
\begin{align}
\mu &= \mathbb{E}[R] = p (1) + q (-1) = p-q \\
\sigma^2 &= \mathbb{E}[R^2] = p (1)^2 + q (-1)^2 = p+q = 1 \\
\end{align}
$$

so the approximation here actually is actually precise: $\lambda^* = p-q$.

## Simple Average Approximation

Simple Average Approximation (SAA) maximizes a finite-sample approximation of the function. Here, $g_N(\lambda; {R_i}) := \frac{1}{N} \sum_{i=1}^N \log\big( 1 + \lambda R_i \big) \xrightarrow{\mathcal{D}} \mathbb{E}\big[ \log\big( 1 + \lambda R \big) \big] = G(\lambda)$.

From \[Homem-de-Mello, 2014\], the optimal value and the optimal argument are both biased estimators converging to the true value.

#### In the binomial case

Given $N$ Bernoulli variates $R_i \sim 2*B(p) - 1$, we want to maximize $\sum_{i=1}^N \log\big( 1+\lambda R_i \big)$ or equivalently $\prod_{i=1}^N (1+\lambda R_i)$.

Using we find that the sampled log-return function exhibits the expected shape, with variance increasing with $\lambda$:

In [44]:
plot_sampled_func(
    univariate_log_return,
    make_bernoulli_return_sampler(0.6),
    x_upper=0.9,
    num_samples=100,
)

alt.Chart(...)

We can use `scipy.optimize` to get the SAA estimate:

In [64]:
estimator = make_saa_estimator(
    sampler=make_bernoulli_return_sampler(0.6),
    func=univariate_log_return,
    func_to_minimize=lambda x, samples: -univariate_log_return(x, samples)
)

In [65]:
plot_benchmark_stats(run_estimator_benchmark(estimator, max_sample_size_order=20))

100%|██████████| 19/19 [00:01<00:00, 12.78it/s] 


alt.Chart(...)

One thing to note is that the estimation becomes ill-conditioned (somewhere just over 10k sample size, with this $p = 0.6$) if we try to use $\prod_{i=1}^N (1+\lambda R_i)$ to avoid the $log$. But simulation speed doesn't seem to be a concern so that shouldn't matter.

The convergence seems to happens relatively quickly, with accuracy within a percentage point by about 10k sample size.

## References

[\[Homem-de-Mello, 2014\]](http://www.optimization-online.org/DB_FILE/2013/06/3920.pdf) Homem-de-Mello, Tito, & Guzin Bayraksan, Monte Carlo Sampling-Based Methods for Stochastic Optimization, 2014-01-22

[\[Rotando, 1992\]](http://www.edwardothorp.com/wp-content/uploads/2016/11/TheKellyCriterionAndTheStockMarket.pdf) Rotando, Louis, & Edward Thorp, The Kelly Criterion and the Stock Market, 1992-10-xx

